In [ ]:
import numpy as np
import random
import plotly.graph_objects as go
import torch

num_samples = 5000
fakeDatasetProperties = dict(
    min_length = 10,
    max_length = 40,
    min_amplitude = 1,
    max_amplitude = 4,
    min_frequency = 1,
    max_frequency = 10,
    sampling_rate = 300)

class SineDataset:
    def __init__(self, dataset_properties):
        self.fakeDatasetProperties = dataset_properties
    def normalize_dataset(self, dataset, conditions, train_split=0.8):
        trainDataset = dataset[:int(len(dataset) * train_split)]
        # Calculate mean and standard deviation for each sample
        means = [torch.mean(sample) for sample in trainDataset]
        stds = [torch.std(sample) for sample in trainDataset]
        # Calculate weights based on the length of each sample
        weights = [len(sample) for sample in trainDataset]
        # Compute the global mean and standard deviation as a weighted average of the individual means and standard deviations
        self.mean_traj = torch.tensor([np.average(means, weights=weights)], dtype=torch.float32)
        self.std_traj = torch.tensor([np.average(stds, weights=weights)], dtype=torch.float32)
        # Normalize each sample using the global mean and standard deviation
        normalized_dataset = [(sample - self.mean_traj) / self.std_traj for sample in dataset]
        train_trajs = normalized_dataset[:int(len(normalized_dataset) * train_split)]
        test_trajs = normalized_dataset[int(len(normalized_dataset) * train_split):]
        # TODO should the conditions be split up like this?
        self.mean_condition = torch.mean(conditions[:int(len(conditions) * train_split)], dim=0)
        self.mean_condition = self.mean_condition.type(torch.float32)
        self.std_condition = torch.std(conditions[:int(len(conditions) * train_split)], dim=0)
        self.std_condition = self.std_condition.type(torch.float32)
        normalized_conditions = [(condition - self.mean_condition) / self.std_condition for condition in conditions]
        train_conditions = normalized_conditions[:int(len(normalized_conditions) * train_split)]
        test_conditions = normalized_conditions[int(len(normalized_conditions) * train_split):]
        self.mean_length = np.array([np.mean(weights)])
        self.std_length = np.array([np.std(weights)])
        return (train_trajs, train_conditions), (test_trajs, test_conditions)
    
    def generate_condition(self, min_length, max_length, min_amplitude, max_amplitude, min_frequency, max_frequency, sampling_rate):
         # randomly select the sample length, amplitude, and frequency
        sample_length = random.randint(min_length, max_length)
        amplitude = random.uniform(min_amplitude, max_amplitude)
        # Ensure each sample includes at least two oscillations
        frequency = random.uniform(max(min_frequency, 2 / (sample_length / sampling_rate)), max_frequency)
        return sample_length, amplitude, frequency
    
    def generate_conditions(self, num_samples, **kwargs):
        conditions = []
        for _ in range(num_samples):
            conditions.append(self.generate_condition(**kwargs)[1:3])
        return conditions
    
    def generate_sine_wave(self, min_length, max_length, min_amplitude, max_amplitude, min_frequency, max_frequency, sampling_rate):
        sample_length, amplitude, frequency = self.generate_condition(min_length, max_length, min_amplitude, max_amplitude, min_frequency, max_frequency, sampling_rate)
        time = torch.arange(sample_length) / sampling_rate
        wave = amplitude * torch.sin(2 * torch.pi * frequency * time)
        wave = wave.unsqueeze(1)
        wave = wave.type(torch.float32)
        return wave, amplitude, frequency

    def generate_dataset(self, num_samples, **kwargs):
        # create an empty list to store the sine waves
        dataset = []
        conditions = torch.zeros((num_samples, 2))
        for i in range(num_samples):
            wave, amplitude, frequency = self.generate_sine_wave(**kwargs)
            dataset.append(wave)
            conditions[i] = torch.tensor([amplitude, frequency], dtype=torch.float32)
        return dataset, conditions

sineDataset = SineDataset(fakeDatasetProperties)
trajs, conditions = sineDataset.generate_dataset(num_samples, **fakeDatasetProperties)
(train_trajs, train_conditions), (test_trajs, test_conditions) = sineDataset.normalize_dataset(trajs, conditions)
print(sineDataset.mean_traj)
print(sineDataset.std_traj)
print(sineDataset.mean_condition)
print(sineDataset.std_condition)

In [ ]:
fig = go.Figure()
# find the shortest frequency in dataset
shortest_freq = fakeDatasetProperties['max_frequency']
for i in range(num_samples):
    if conditions[i][1] < shortest_freq:
        shortest_freq = conditions[i][1]
        index = i
# find highest frequency in dataset
highest_freq = fakeDatasetProperties['min_frequency']
fig.add_trace(go.Scatter(y=np.squeeze(trajs[index]), mode='markers', name='lowest frequency'))
for i in range(num_samples):
    if conditions[i][1] > highest_freq:
        highest_freq = conditions[i][1]
        index = i
fig.add_trace(go.Scatter(y=np.squeeze(trajs[index]), mode='markers', name='highest frequency'))
fig.show()
fig = go.Figure()
for i in range(100):
    fig.add_trace(go.Scatter(y=np.squeeze(trajs[i]), mode='lines'))
fig.update_layout(title='First 100 samples from the dataset', xaxis_title='Time', yaxis_title='Amplitude')
fig.show()

In [17]:
from src.mouseGAN.LR_schedulers import *
from src.mouseGAN.model_config import GAN_DATASET, Config, LR_SCHEDULERS, LOSS_FUNC, \
    C_MiniBatchDisc, C_Discriminator, C_Generator, C_EMA_Plateua_Sch, \
    C_Step_Sch, C_LossGap_Sch
from src.mouseGAN.models import MouseGAN
from src.mouseGAN.experimentTracker import initialize_wandb
from src.mouseGAN.dataProcessing import MouseGAN_Data
from src.mouseGAN.dataset import getDataloader


IN_COLAB = False
LOAD_PRETRAINED = False
BATCH_SIZE = 256
num_epochs = 1000
num_feats = train_trajs[0].shape[1]
latent_dim = 1
num_target_feats = train_conditions[0].shape[0]
numBatches = len(train_trajs)//BATCH_SIZE
MAX_SEQ_LEN = max([len(traj) for traj in train_trajs + test_trajs])

D_config = C_Discriminator(lr=0.01, bidirectional=True, hidden_units=128, 
                            num_lstm_layers=1, 
                            useEndDeviationLoss=False,
                            gradient_maxNorm = 1.0,
                            spectral_norm = True)
G_config = C_Generator(lr=0.0002, hidden_units=128, num_lstm_layers=2, drop_prob=0.4,
                layer_normalization = True,
                residual_connections = True,
                gradient_maxNorm = 1.0,
                useSeqLengthLoss=False,
                useOutsideTargetLoss=False,
                usePathLengthLoss=False)

D_sch_config = C_LossGap_Sch(cooldown=int(numBatches/4), lr_shrinkMin=0.1, lr_growthMax=2.0, 
                            discLossDecay=0.8, lr_max = D_config.lr, lr_min = 0.0001, restart_after=int(numBatches))
# G_sch_config = C_EMA_Plateua_Sch(patience=BATCH_SIZE, cooldown=int(BATCH_SIZE/8), factor=0.5, ema_alpha=0.4)

config = Config(num_epochs, BATCH_SIZE, num_feats, latent_dim, num_target_feats, MAX_SEQ_LEN,
                discriminator=D_config, generator=G_config, 
                D_lr_scheduler=D_sch_config, #G_lr_scheduler=G_sch_config,
                locationMSELoss = True)

## verifying the mean trajectory is centered around zero (even class distribution)
# dataset.plotMeanPath()
trainLoader = getDataloader(train_trajs, train_conditions, config.BATCH_SIZE)
testLoader = getDataloader(test_trajs, test_conditions, config.BATCH_SIZE)

 
# if IN_COLAB:
# run = initialize_wandb(config, tempProjectName='sineGAN')
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
gan = MouseGAN(sineDataset, trainLoader, testLoader, device, config, IN_COLAB=IN_COLAB, verbose=True, printBatch=False, dataType=GAN_DATASET.SINE_WAVE)
if LOAD_PRETRAINED:
    gan.loadPretrained(startingEpoch=300)

gan.visualTrainingVerfication(samples=10)

# print(gan.discriminator)
# print(gan.generator)

# gan.find_learning_rates_for_GAN()
gan.train(modelSaveInterval=20, catchErrors=False, visualCheckInterval=5)
# if IN_COLAB:
#     wandb.finish()

{'epoch': 0, 'd_loss': '0.51430', 'g_loss': '2.68431', 'epochTime': '9.26544', 'val_accuracy': '0.94336', 'val_d_loss': '0.17780', 'val_g_loss': '4.50315'}
{'epoch': 1, 'd_loss': '0.40881', 'g_loss': '2.15941', 'epochTime': '8.32876', 'val_accuracy': '0.72559', 'val_d_loss': '0.60434', 'val_g_loss': '1.37676'}
{'epoch': 2, 'd_loss': '0.42276', 'g_loss': '2.68985', 'epochTime': '8.17579', 'val_accuracy': '0.84424', 'val_d_loss': '0.51086', 'val_g_loss': '1.65134'}
{'epoch': 3, 'd_loss': '0.43961', 'g_loss': '1.89595', 'epochTime': '8.37616', 'val_accuracy': '0.79395', 'val_d_loss': '0.55676', 'val_g_loss': '1.66807'}
{'epoch': 4, 'd_loss': '0.47406', 'g_loss': '2.82311', 'epochTime': '8.32939', 'val_accuracy': '0.92871', 'val_d_loss': '0.40996', 'val_g_loss': '1.78750'}


{'epoch': 5, 'd_loss': '0.29019', 'g_loss': '2.63093', 'epochTime': '8.45166', 'val_accuracy': '0.70215', 'val_d_loss': '0.61511', 'val_g_loss': '1.40911'}
{'epoch': 6, 'd_loss': '0.43825', 'g_loss': '2.97865', 'epochTime': '8.17122', 'val_accuracy': '0.66553', 'val_d_loss': '1.29251', 'val_g_loss': '0.87727'}
{'epoch': 7, 'd_loss': '0.37100', 'g_loss': '3.41881', 'epochTime': '8.26745', 'val_accuracy': '0.96777', 'val_d_loss': '0.29772', 'val_g_loss': '1.95197'}
{'epoch': 8, 'd_loss': '0.53395', 'g_loss': '2.18890', 'epochTime': '7.90163', 'val_accuracy': '0.83984', 'val_d_loss': '0.50889', 'val_g_loss': '5.67026'}
{'epoch': 9, 'd_loss': '0.39535', 'g_loss': '3.20647', 'epochTime': '8.12220', 'val_accuracy': '0.77686', 'val_d_loss': '0.50759', 'val_g_loss': '1.93193'}


{'epoch': 10, 'd_loss': '0.37636', 'g_loss': '2.80136', 'epochTime': '7.97841', 'val_accuracy': '0.78418', 'val_d_loss': '0.63992', 'val_g_loss': '2.04099'}
{'epoch': 11, 'd_loss': '0.43433', 'g_loss': '2.64082', 'epochTime': '7.63638', 'val_accuracy': '0.84277', 'val_d_loss': '0.51396', 'val_g_loss': '2.21460'}
{'epoch': 12, 'd_loss': '0.47575', 'g_loss': '1.88150', 'epochTime': '7.61589', 'val_accuracy': '0.90576', 'val_d_loss': '0.50842', 'val_g_loss': '1.77075'}
{'epoch': 13, 'd_loss': '0.48745', 'g_loss': '1.99278', 'epochTime': '7.35399', 'val_accuracy': '0.75293', 'val_d_loss': '0.64664', 'val_g_loss': '1.32211'}
{'epoch': 14, 'd_loss': '0.45413', 'g_loss': '2.09112', 'epochTime': '7.53375', 'val_accuracy': '0.86816', 'val_d_loss': '0.45959', 'val_g_loss': '1.94374'}


{'epoch': 15, 'd_loss': '0.36064', 'g_loss': '2.84588', 'epochTime': '7.69992', 'val_accuracy': '0.90479', 'val_d_loss': '0.35120', 'val_g_loss': '2.38868'}
{'epoch': 16, 'd_loss': '0.31338', 'g_loss': '3.09784', 'epochTime': '7.83231', 'val_accuracy': '0.83545', 'val_d_loss': '0.46660', 'val_g_loss': '1.94746'}
{'epoch': 17, 'd_loss': '0.36611', 'g_loss': '2.48886', 'epochTime': '7.73259', 'val_accuracy': '0.88135', 'val_d_loss': '0.48583', 'val_g_loss': '1.48393'}
{'epoch': 18, 'd_loss': '0.34692', 'g_loss': '2.25964', 'epochTime': '7.58564', 'val_accuracy': '0.81641', 'val_d_loss': '0.47513', 'val_g_loss': '3.06358'}
{'epoch': 19, 'd_loss': '0.31869', 'g_loss': '2.60459', 'epochTime': '7.64986', 'val_accuracy': '0.91260', 'val_d_loss': '0.34045', 'val_g_loss': '1.93386'}
	Saved generator: /Users/mnann/Documents/Code/AuthenticCursor/data/local/ganModels/g20.pt
	Saved discriminator: /Users/mnann/Documents/Code/AuthenticCursor/data/local/ganModels/d20.pt


{'epoch': 20, 'd_loss': '0.31778', 'g_loss': '3.04516', 'epochTime': '7.16539', 'val_accuracy': '0.84814', 'val_d_loss': '0.42458', 'val_g_loss': '1.97401'}
{'epoch': 21, 'd_loss': '0.28955', 'g_loss': '2.45788', 'epochTime': '8.28180', 'val_accuracy': '0.84717', 'val_d_loss': '0.42466', 'val_g_loss': '1.78981'}
{'epoch': 22, 'd_loss': '0.30671', 'g_loss': '3.22369', 'epochTime': '8.10463', 'val_accuracy': '0.90381', 'val_d_loss': '0.30252', 'val_g_loss': '2.74732'}
{'epoch': 23, 'd_loss': '0.26115', 'g_loss': '3.15664', 'epochTime': '8.12122', 'val_accuracy': '0.89990', 'val_d_loss': '0.31586', 'val_g_loss': '2.50248'}
{'epoch': 24, 'd_loss': '0.16600', 'g_loss': '3.35285', 'epochTime': '8.09832', 'val_accuracy': '0.94727', 'val_d_loss': '0.20404', 'val_g_loss': '2.66374'}


...

{'epoch': 975, 'd_loss': '0.01478', 'g_loss': '3.99762', 'epochTime': '11.46265', 'val_accuracy': '0.97168', 'val_d_loss': '0.01739', 'val_g_loss': '4.05187'}
{'epoch': 976, 'd_loss': '0.01265', 'g_loss': '4.08718', 'epochTime': '11.97579', 'val_accuracy': '0.97168', 'val_d_loss': '0.01754', 'val_g_loss': '4.02125'}
{'epoch': 977, 'd_loss': '0.01031', 'g_loss': '3.87896', 'epochTime': '11.76855', 'val_accuracy': '0.93994', 'val_d_loss': '0.14326', 'val_g_loss': '3.54521'}
{'epoch': 978, 'd_loss': '0.01143', 'g_loss': '3.84059', 'epochTime': '12.15220', 'val_accuracy': '0.94141', 'val_d_loss': '0.12008', 'val_g_loss': '3.65502'}
{'epoch': 979, 'd_loss': '0.00836', 'g_loss': '4.12131', 'epochTime': '12.32592', 'val_accuracy': '0.95166', 'val_d_loss': '0.08752', 'val_g_loss': '3.78542'}
	Saved generator: /Users/mnann/Documents/Code/AuthenticCursor/data/local/ganModels/g980.pt
	Saved discriminator: /Users/mnann/Documents/Code/AuthenticCursor/data/local/ganModels/d980.pt


{'epoch': 980, 'd_loss': '0.00680', 'g_loss': '4.02897', 'epochTime': '12.39450', 'val_accuracy': '0.97217', 'val_d_loss': '0.01778', 'val_g_loss': '3.79272'}
{'epoch': 981, 'd_loss': '0.00551', 'g_loss': '3.85418', 'epochTime': '11.58688', 'val_accuracy': '0.97217', 'val_d_loss': '0.01640', 'val_g_loss': '3.78705'}
{'epoch': 982, 'd_loss': '0.00586', 'g_loss': '3.99225', 'epochTime': '12.19625', 'val_accuracy': '0.97119', 'val_d_loss': '0.02002', 'val_g_loss': '4.02705'}
{'epoch': 983, 'd_loss': '0.00366', 'g_loss': '4.10198', 'epochTime': '11.75594', 'val_accuracy': '0.97314', 'val_d_loss': '0.01414', 'val_g_loss': '4.02906'}
{'epoch': 984, 'd_loss': '0.00624', 'g_loss': '3.91688', 'epochTime': '11.73816', 'val_accuracy': '0.96777', 'val_d_loss': '0.03163', 'val_g_loss': '3.76058'}


{'epoch': 985, 'd_loss': '0.00347', 'g_loss': '3.89251', 'epochTime': '12.16028', 'val_accuracy': '0.97168', 'val_d_loss': '0.01716', 'val_g_loss': '3.89771'}
{'epoch': 986, 'd_loss': '0.00404', 'g_loss': '4.09469', 'epochTime': '13.11039', 'val_accuracy': '0.97021', 'val_d_loss': '0.02425', 'val_g_loss': '3.94749'}
{'epoch': 987, 'd_loss': '0.00401', 'g_loss': '4.02706', 'epochTime': '12.55008', 'val_accuracy': '0.96875', 'val_d_loss': '0.02931', 'val_g_loss': '3.73628'}
{'epoch': 988, 'd_loss': '0.00267', 'g_loss': '3.87830', 'epochTime': '12.44545', 'val_accuracy': '0.97119', 'val_d_loss': '0.02125', 'val_g_loss': '3.76785'}
{'epoch': 989, 'd_loss': '0.00329', 'g_loss': '4.00376', 'epochTime': '12.75125', 'val_accuracy': '0.97363', 'val_d_loss': '0.01211', 'val_g_loss': '4.01201'}


{'epoch': 990, 'd_loss': '0.00412', 'g_loss': '4.10409', 'epochTime': '12.19490', 'val_accuracy': '0.97363', 'val_d_loss': '0.01269', 'val_g_loss': '4.00064'}
{'epoch': 991, 'd_loss': '0.01282', 'g_loss': '3.88119', 'epochTime': '11.96676', 'val_accuracy': '0.95361', 'val_d_loss': '0.08847', 'val_g_loss': '3.64346'}
{'epoch': 992, 'd_loss': '0.01282', 'g_loss': '3.86072', 'epochTime': '13.18944', 'val_accuracy': '0.93652', 'val_d_loss': '0.14448', 'val_g_loss': '3.95706'}
{'epoch': 993, 'd_loss': '0.01856', 'g_loss': '4.10006', 'epochTime': '12.75482', 'val_accuracy': '0.96777', 'val_d_loss': '0.03047', 'val_g_loss': '3.97835'}
{'epoch': 994, 'd_loss': '0.01247', 'g_loss': '4.00120', 'epochTime': '13.01048', 'val_accuracy': '0.94482', 'val_d_loss': '0.13336', 'val_g_loss': '3.56959'}


{'epoch': 995, 'd_loss': '0.02342', 'g_loss': '3.82534', 'epochTime': '12.39975', 'val_accuracy': '0.97656', 'val_d_loss': '0.00478', 'val_g_loss': '3.87852'}
{'epoch': 996, 'd_loss': '0.00486', 'g_loss': '4.03988', 'epochTime': '12.10914', 'val_accuracy': '0.97607', 'val_d_loss': '0.00625', 'val_g_loss': '4.15112'}
{'epoch': 997, 'd_loss': '0.00552', 'g_loss': '4.14777', 'epochTime': '12.07145', 'val_accuracy': '0.97607', 'val_d_loss': '0.00576', 'val_g_loss': '4.14108'}
{'epoch': 998, 'd_loss': '0.00396', 'g_loss': '3.89032', 'epochTime': '11.72141', 'val_accuracy': '0.97656', 'val_d_loss': '0.00436', 'val_g_loss': '3.82181'}
{'epoch': 999, 'd_loss': '0.00445', 'g_loss': '3.84513', 'epochTime': '12.14048', 'val_accuracy': '0.97656', 'val_d_loss': '0.00059', 'val_g_loss': '4.02232'}
	Saved generator: /Users/mnann/Documents/Code/AuthenticCursor/data/local/ganModels/g999.pt
	Saved discriminator: /Users/mnann/Documents/Code/AuthenticCursor/data/local/ganModels/d999.pt


In [ ]:
gan.visualTrainingVerfication(samples=10)

In [ ]:
gan.train(modelSaveInterval=3, catchErrors=False)

In [ ]:
# gan.save_models('final')
gan.loadPretrained(startingEpoch=99)

In [ ]:
for epoch in ['final']:
    gan.loadPretrained(startingEpoch=epoch)
    gan.visualTrainingVerfication()

In [ ]:
a = torch.tensor(1.5)
a.requires_grad_()
b = torch.greater(a, 1.0)
# b = torch.round(a)
b.backward()
a.grad